In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

<frozen importlib._bootstrap>:228: RuntimeWarning: scipy._lib.messagestream.MessageStream size changed, may indicate binary incompatibility. Expected 56 from C header, got 64 from PyObject


In [2]:
#data1 = np.loadtxt("../with_heparin/avclust.xvg", skiprows = 17)
#data2 = np.loadtxt("../without_heparin_large/avclust.xvg", skiprows = 17)

In [3]:
#len(data2)

In [4]:
#plt.plot(data1[:,0], data1[:,1]//107)
#plt.plot(data2[:,0], data2[:,1]//107)

In [5]:
#data1 = np.loadtxt("../with_heparin/maxclust.xvg", skiprows = 17)

In [6]:
#data1

In [7]:
#data1 = np.loadtxt("../with_heparin/maxclust.ndx", skiprows = 1)

In [8]:
import subprocess, os

In [298]:
# Function to get surface values of cyllinder started at point p0 and ended at p1 with radi R..
def getCoordsCyllinder(p0, p1, R = 1):
    """
        input : 
            p0 : starting point of the cyllinder
            p1 : ending point of the cyllinder
            R : radi of the base of cyllinder
        output : 
            X, Y, Z : meshgrid of surface of the required cyllinder
    """
    
    #vector in direction of axis
    v = p1 - p0
    #find magnitude of vector
    mag = np.linalg.norm(v)
    #unit vector in direction of axis
    v = v / mag
    #make some vector not in the same direction as v
    not_v = np.array([1, 0, 0])
    if (v == not_v).all():
        not_v = np.array([0, 1, 0])
    #make vector perpendicular to v
    n1 = np.cross(v, not_v)
    #normalize n1
    n1 /= np.linalg.norm(n1)
    #make unit vector perpendicular to v and n1
    n2 = np.cross(v, n1)
    #surface ranges over t from 0 to length of axis and 0 to 2*pi
    t = np.linspace(0, mag, 100)
    theta = np.linspace(0, 2 * np.pi, 100)
    #use meshgrid to make 2d arrays
    t, theta = np.meshgrid(t, theta)
    #generate coordinates for surface
    X, Y, Z = [p0[i] + v[i] * t + R * np.sin(theta) * n1[i] + R * np.cos(theta) * n2[i] for i in [0, 1, 2]]
    return X, Y, Z
def circle(x, y, z, r):
    """Create a circular mesh located at x, y, z with radius r"""
    r_discr = np.linspace(0, r, 2)
    theta_discr = np.linspace(0, 2*np.pi, 100)
    r_grid, theta_grid = np.meshgrid(r_discr, theta_discr)
    x_circle = r_grid * np.cos(theta_grid) + x
    y_circle = r_grid * np.sin(theta_grid) + y
    z_circle = np.zeros_like(x_circle) + z
    return x_circle, y_circle, z_circle

def cylinder(x, y, z, r, dz):
    """Create a cylindrical mesh located at x, y, z, with radius r and height dz"""
    center_z = np.linspace(0, dz, 100)
    theta = np.linspace(0, 2*np.pi, 100)
    theta_grid, z_grid = np.meshgrid(theta, center_z)
    x_grid = r * np.cos(theta_grid) + x
    y_grid = r * np.sin(theta_grid) + y
    z_grid = z_grid + z
    return x_grid, y_grid, z_grid

def addAxis(fig, p0, p1, R=1):
    #p0 = np.array([COM[0], COM[1], COM[2]])
    #p1 = np.array([COM[0]+dx0, COM[1]+dy0, COM[2]+dz0])
    x_cyl, y_cyl, z_cyl = getCoordsCyllinder(p0, p1, R)

    colorscale = [[0, 'black'],
                 [1, 'black']]
    colorscale_cone = [[0, 'red'],
                 [1, 'red']]
    fig.add_trace(go.Surface(x=x_cyl, y=y_cyl, z=z_cyl, colorscale=colorscale, showscale=False, opacity=0.8))
    vec = p1 - p0
    fig.add_trace(go.Cone(x = [p1[0]], y = [p1[1]], z = [p1[2]],
                          u = [vec[0]], v = [vec[1]] , w = [vec[2]],
                         showscale=False, colorscale=colorscale_cone))
    #fig.update_layout(scene_camera_eye_z= 0.55)
    #fig.layout.scene.camera.projection.type = "orthographic" #commenting this line you get a fig with perspective proj

    #fig.show()


In [10]:
#help(os.remove)
import tqdm.auto as tqdm

In [216]:
index_list = []
os.chdir("/home/dibya/Dibyendu/Project_Heparin/CS12/with_heparin")
file_pattern = ["nclust", "avclust", "maxclust", "temp", "histo-clust", "csize", "csizew"]
for i in tqdm.trange(200, 285):
    com1 = f"/home/dibya/Soft/gmx19/bin/gmx clustsize -f pbc_cluster.xtc -s pbc_cluster.tpr -n pbc_cluster.ndx -b {i*1000} -e {i*1000 + 1}"
    com2 = "printf 2 | "
    subprocess.call(com2 + com1 + " -quiet", shell = True,  stdout=subprocess.DEVNULL, stderr=subprocess.DEVNULL)
    data1 = np.loadtxt("maxclust.ndx", skiprows = 1)
    index_list.append(data1)
    allFiles = os.listdir()
    #print(allFiles)
    for file in allFiles:
        for pattern in file_pattern:
            if pattern in file:
                try:
                    os.remove(file)
                except:
                    pass
                    #raise FileNotFoundError

  0%|          | 0/85 [00:00<?, ?it/s]

In [203]:
import MDAnalysis as mda

In [204]:
u = mda.Universe("pbc_cluster.gro", "pbc_cluster.xtc", reset_offset = True)

In [219]:
u.trajectory[2000]
sel = u.select_atoms(f"id {int(index_list[0][0])} and resname LIG")
for i in index_list[0][1:]:
    sel += u.select_atoms(f"id {int(i)} and resname LIG")

In [222]:
gmx = "/home/dibya/Soft/gmx19/bin/gmx"
tc_path = "/home/dibya/Dibyendu/Project_Heparin/CS12/without_heparin/topol_corrector.py"
## Frame
sel.write("selection.gro")
## index
command1 = f'printf "ri 1\n q\n" | {gmx} make_ndx -f selection.gro -o select.ndx'
subprocess.call(command1 + " -quiet", shell = True,  stdout=subprocess.DEVNULL, stderr=subprocess.DEVNULL)
##topology
command2 = f"python {tc_path} -f test.top -o select.top -i selection.gro"
subprocess.call(command2 , shell = True, stdout=subprocess.DEVNULL, stderr=subprocess.DEVNULL)
## tpr
command3 = f"{gmx} grompp -f test.mdp -c selection.gro -p select.top -o select.tpr -maxwarn 1"
subprocess.call(command3 , shell = True,  stdout=subprocess.DEVNULL, stderr=subprocess.DEVNULL)
## centered..
command30 = "printf '3\n 0\n' | " 
command31 = f"{gmx} trjconv -f selection.gro -s select.tpr -n select.ndx"
command32 = " -center -o centered_select.gro -pbc mol -ur compact"
subprocess.call(command30 + command31 + command32 + " -quiet", shell = True,  stdout=subprocess.DEVNULL, stderr=subprocess.DEVNULL)

0

In [224]:
# Define the gyration tensor here! :)
def gyration(coord):   
    gyr = np.zeros((3,3))
    # Coordinate system is shifted such that origin is at COM
    COM = coord.mean(axis=0)
    shifted = coord - COM
    for i in range(len(coord)):
        gyr[0,0] += shifted[i,0]**2
        gyr[1,1] += shifted[i,1]**2
        gyr[2,2] += shifted[i,2]**2
        gyr[0,1] += shifted[i,0]*shifted[i,1]
        gyr[0,2] += shifted[i,0]*shifted[i,2]
        gyr[1,2] += shifted[i,1]*shifted[i,2]
        
    gyr /= len(coord)
    gyr[1,0] = gyr[0,1]
    gyr[2,0] = gyr[0,2]
    gyr[2,1] = gyr[1,2]
    return gyr



In [225]:
pos = mda.Universe("centered_select.gro").atoms.positions
g_mat = gyration(pos)

In [230]:
w, v = np.linalg.eig(g_mat)

In [227]:
import plotly.graph_objects as go

In [240]:
def PlotPC(data, opacity = 0.01, color = f"rgb(0.0, 0.0, 140)"):
    x, y, z = data[:,0], data[:,1], data[:,2]
    fig = go.Figure(data=[go.Scatter3d(x=x, y=y, z=z,
                                       mode='markers',marker=dict(
                color =  color,
                size=5,
                opacity=opacity,
                #line=dict(
                #    color='MediumPurple',
                #    width=0.1
                #)
            ))])
    fig.layout.scene.camera.projection.type = 'orthographic'
    #for template in ["plotly", "plotly_white", "plotly_dark", "ggplot2", "seaborn", "simple_white", "none"]:
    fig.update_layout(template="simple_white")
    fig.update_layout(
        autosize=False,
        width=500,
        height=500,
        margin=dict(
            l=0,
            r=0,
            b=10,
            t=40,
            pad=10
        ),
        paper_bgcolor="LightSteelBlue",
    )
    #legend
    fig.update_layout(showlegend=False)

    #x axis
    #fig.update_xaxes(visible=False, showline = False, zeroline = False, showticklabels=False)
    fig.update_layout(
        scene=dict(
            xaxis=dict(showticklabels=False,ticks="",title = ""),
            yaxis=dict(showticklabels=False,ticks="", title = ""),
            zaxis=dict(showticklabels=False,ticks="", title = ""),
        )
    )
    #y axis    
    #fig.update_yaxes(visible=False,  showline = False, zeroline = False, showticklabels=False)
    #fig.show()
    return fig

In [241]:
#pos = sel.wrap(compound='atoms', center="com", inplace = False)

In [299]:
fig = PlotPC(pos)
p0 = np.array([COM[0], COM[1], COM[2]])
p1 = np.array([COM[0]+dx0, COM[1]+dy0, COM[2]+dz0])
addAxis(fig, p0, p1, R=1)
p0 = np.array([COM[0], COM[1], COM[2]])
p1 = np.array([COM[0]+dx1, COM[1]+dy1, COM[2]+dz1])
addAxis(fig, p0, p1, R=1)
p0 = np.array([COM[0], COM[1], COM[2]])
p1 = np.array([COM[0]+dx2, COM[1]+dy2, COM[2]+dz2])
addAxis(fig, p0, p1, R=1)
fig.show()